In [2]:
## This is where I preprocess the crema data

In [5]:
pip install opencv-python opencv-python-headless numpy pandas moviepy

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [ ]:
pip install --upgrade numpy pandas

In [2]:
import os
import cv2
import pandas as pd
import numpy as np
from moviepy import VideoFileClip as mp
from PIL import Image
import subprocess

In [3]:
input_vids = "/home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash"
output_gifs = "./CremaGifs"
metadata_file = "~/Thesis/data/crema-d/CREMA-D/processedResults/tabulatedVotes.csv"
os.makedirs(output_gifs, exist_ok=True)

In [4]:
# Check and download Git LFS files
def check_and_download_git_lfs(video_dir):
    for video_file in os.listdir(video_dir):
        file_path = os.path.join(video_dir, video_file)
        with open(file_path, 'r') as file:
            if 'version https://git-lfs.github.com/spec/v1' in file.read():
                # print(f"Downloading actual file for {video_file}...")
                subprocess.run(["/home/jecroisp/bin/git-lfs-3.4.0/git-lfs", "pull"], cwd=video_dir)
                print(f"Downloaded {video_file}.")


In [5]:
metadata = pd.read_csv(metadata_file)

In [6]:
df = pd.DataFrame(metadata)
df.head(10)

Unnamed: 0  A  D  F  H   N  S         fileName  numResponses  agreement  \
0      100001  0  0  0  1  10  0  1001_IEO_NEU_XX            11   0.909091   
1      100002  0  0  0  3   6  0  1001_IEO_HAP_LO             9   0.666667   
2      100003  0  0  0  4   7  0  1001_IEO_HAP_MD            11   0.636364   
3      100004  2  0  0  6   2  0  1001_IEO_HAP_HI            10   0.600000   
4      100005  1  1  0  0   7  1  1001_IEO_SAD_LO            10   0.700000   
5      100006  0  1  1  0   8  0  1001_IEO_SAD_MD            10   0.800000   
6      100007  1  0  0  1   7  0  1001_IEO_SAD_HI             9   0.777778   
7      100008  0  1  0  2   7  0  1001_IEO_ANG_LO            10   0.700000   
8      100009  5  5  0  0   1  1  1001_IEO_ANG_MD            12   0.416667   
9      100010  2  6  0  0   1  0  1001_IEO_ANG_HI             9   0.666667   

   ... meanSadResp  medianEmoResp  meanEmoRespNorm  meanAngerRespNorm  \
0  ...        -1.0           87.0        66.171320          -1.000000   
1  ...        -1.0           72.0        53.816160          -1.000000   
2  ...        -1.0           60.0        61.874713          -1.000000   
3  ...        -1.0           69.5        52.927309          84.420185   
4  ...         6.0           80.0        59.486728          12.941176   
5  ...        -1.0           45.0        35.346789          -1.000000   
6  ...        -1.0           61.0        46.297591           0.000000   
7  ...        -1.0           50.0        50.212180          -1.000000   
8  ...        71.0           54.5        41.872207          30.192524   
9  ...        -1.0           81.0        70.072041          78.706419   

   meanDisgustRespNorm  meanFearRespNorm  meanHappyRespNorm  \
0            -1.000000         -1.000000          97.894737   
1            -1.000000         -1.000000          36.292735   
2            -1.000000         -1.000000          55.165230   
3            -1.000000         -1.000000          56.542708   
4            94.936709         -1.000000          -1.000000   
5            49.056604          2.298851          -1.000000   
6            -1.000000         -1.000000          27.835052   
7            27.083333         -1.000000          29.629630   
8            50.618954         -1.000000          -1.000000   
9            62.205923         -1.000000          -1.000000   

   meanNeutralRespNorm  meanSadRespNorm  medianEmoRespNorm  
0            62.998978        -1.000000          83.333333  
1            62.577873        -1.000000          53.846154  
2            65.708703        -1.000000          61.111111  
3            10.588235        -1.000000          66.308140  
4            69.123485         3.125000          75.182073  
5            37.764055        -1.000000          36.333907  
6            55.549038        -1.000000          50.649351  
7            59.397030        -1.000000          47.803777  
8            51.136364        47.272727          40.328874  
9           100.000000        -1.000000          77.419355  

[10 rows x 27 columns]

In [7]:
def video_to_gif(input_vids, output_gifs, start_time=0, duration=None):
    clip = mp(input_vids)
    if duration:
        clip = clip.subclipped(start_time, start_time + duration)
    clip = clip.resized(height=360)  # Resize for smaller GIFs
    clip.write_gif(output_gifs, fps=15)  # Adjust FPS for smoother animation

In [11]:
# Check and download missing Git LFS files
check_and_download_git_lfs(input_vids)

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xe0 in position 16: invalid continuation byte

In [7]:
# Function to convert .flv to .mp4
def convert_flv_to_mp4(input_path, output_path):
    clip = mp(input_path)
    clip.write_videofile(output_path, codec='libx264', audio_codec='aac')

In [ ]:
for video_file in os.listdir(input_vids):
    if video_file.endswith(".flv"):  # Check file extension
        video_path = os.path.join(input_vids, video_file)
        mp4_name = video_file.replace(".flv", ".mp4")
        mp4_path = os.path.join(input_vids, mp4_name)
        gif_name = video_file.replace(".flv", ".gif")
        output_gif_path = os.path.join(output_gifs, gif_name)

        # Convert .flv to .mp4
        print(f"Converting {video_file} to {mp4_name}...")
        try:
            convert_flv_to_mp4(video_path, mp4_path)
            print(f"Successfully converted {video_file} to {mp4_name}.")
        except Exception as e:
            print(f"Failed to convert {video_file}: {e}")
            import traceback
            traceback.print_exc()
            continue  # Skip to the next video if conversion fails

        # Convert .mp4 to GIF
        print(f"Processing {mp4_name} -> {gif_name}...")
        try:
            video_to_gif(mp4_path, output_gif_path)
            print(f"Successfully processed {mp4_name} into {gif_name}.")
        except Exception as e:
            print(f"Failed to process {mp4_name}: {e}")
            import traceback
            traceback.print_exc()

print("All videos have been processed into GIFs!")



Converting 1010_IEO_DIS_HI.flv to 1010_IEO_DIS_HI.mp4...
{'video_found': True, 'audio_found': True, 'metadata': {'audiodelay': '0', 'canSeekToEnd': 'true'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'data', 'language': None, 'default': True}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': False, 'fps': 44100, 'bitrate': 262}, {'input_number': 0, 'stream_number': 2, 'stream_type': 'video', 'language': None, 'default': False, 'size': [480, 360], 'bitrate': 823, 'fps': 29.97002997002997, 'codec_name': 'vp6f', 'profile': None}], 'input_number': 0}], 'duration': 3.3, 'bitrate': 1014, 'start': 0.0, 'default_data_input_number': 0, 'default_data_stream_number': 0, 'video_codec_name': 'vp6f', 'video_profile': None, 'video_size': [480, 360], 'video_bitrate': 823, 'video_fps': 29.97002997002997, 'video_duration': 3.3, 'video_n_frames': 98, 'audio_bitrate': 262}
/home/jecroisp/.local/lib/python3.10/site-packages/ima

MoviePy - Done.
MoviePy - Writing video /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1010_IEO_DIS_HI.mp4



MoviePy - Done !
MoviePy - video ready /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1010_IEO_DIS_HI.mp4
Successfully converted 1010_IEO_DIS_HI.flv to 1010_IEO_DIS_HI.mp4.
Processing 1010_IEO_DIS_HI.mp4 -> 1010_IEO_DIS_HI.gif...
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf58.29.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [480, 360], 'bitrate': 255, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'handler_name': 'VideoHandler'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 133, 'metadata': {'handler_name': 'SoundHandler'}}], 'input_number': 0}], 'duration': 3.32, 'bitrate': 397, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, 'v

Successfully processed 1010_IEO_DIS_HI.mp4 into 1010_IEO_DIS_HI.gif.
Converting 1053_IWW_ANG_XX.flv to 1053_IWW_ANG_XX.mp4...
{'video_found': True, 'audio_found': True, 'metadata': {'audiodelay': '0', 'canSeekToEnd': 'true'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'data', 'language': None, 'default': True}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': False, 'fps': 44100, 'bitrate': 262}, {'input_number': 0, 'stream_number': 2, 'stream_type': 'video', 'language': None, 'default': False, 'size': [480, 360], 'bitrate': 823, 'fps': 29.97002997002997, 'codec_name': 'vp6f', 'profile': None}], 'input_number': 0}], 'duration': 1.84, 'bitrate': 1025, 'start': 0.0, 'default_data_input_number': 0, 'default_data_stream_number': 0, 'video_codec_name': 'vp6f', 'video_profile': None, 'video_size': [480, 360], 'video_bitrate': 823, 'video_fps': 29.97002997002997, 'video_duration': 1.84, 'video_n_frames': 55, 'audi

MoviePy - Done.
MoviePy - Writing video /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1053_IWW_ANG_XX.mp4



...

MoviePy - Done.
MoviePy - Writing video /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1053_WSI_NEU_XX.mp4



MoviePy - Done !
MoviePy - video ready /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1053_WSI_NEU_XX.mp4
Successfully converted 1053_WSI_NEU_XX.flv to 1053_WSI_NEU_XX.mp4.
Processing 1053_WSI_NEU_XX.mp4 -> 1053_WSI_NEU_XX.gif...
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf58.29.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [480, 360], 'bitrate': 272, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'handler_name': 'VideoHandler'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 138, 'metadata': {'handler_name': 'SoundHandler'}}], 'input_number': 0}], 'duration': 2.26, 'bitrate': 420, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, 'v

Successfully processed 1053_WSI_NEU_XX.mp4 into 1053_WSI_NEU_XX.gif.
Converting 1064_IEO_DIS_MD.flv to 1064_IEO_DIS_MD.mp4...
{'video_found': True, 'audio_found': True, 'metadata': {'audiodelay': '0', 'canSeekToEnd': 'true'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'data', 'language': None, 'default': True}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': False, 'fps': 44100, 'bitrate': 262}, {'input_number': 0, 'stream_number': 2, 'stream_type': 'video', 'language': None, 'default': False, 'size': [480, 360], 'bitrate': 823, 'fps': 29.97002997002997, 'codec_name': 'vp6f', 'profile': None}], 'input_number': 0}], 'duration': 61.76, 'bitrate': 1106, 'start': 0.0, 'default_data_input_number': 0, 'default_data_stream_number': 0, 'video_codec_name': 'vp6f', 'video_profile': None, 'video_size': [480, 360], 'video_bitrate': 823, 'video_fps': 29.97002997002997, 'video_duration': 61.76, 'video_n_frames': 1850, '

MoviePy - Done.
MoviePy - Writing video /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1064_IEO_DIS_MD.mp4



MoviePy - Done !
MoviePy - video ready /home/jecroisp/Thesis/data/crema-d/CREMA-D/VideoFlash/1064_IEO_DIS_MD.mp4
Successfully converted 1064_IEO_DIS_MD.flv to 1064_IEO_DIS_MD.mp4.
Processing 1064_IEO_DIS_MD.mp4 -> 1064_IEO_DIS_MD.gif...
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf58.29.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [480, 360], 'bitrate': 327, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'handler_name': 'VideoHandler'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 125, 'metadata': {'handler_name': 'SoundHandler'}}], 'input_number': 0}], 'duration': 61.78, 'bitrate': 462, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, '

In [1]:
# Merge Metadata for Annotations
metadata['GIF_Name'] = metadata['fileName'].str.replace(".flv", ".gif")
metadata.to_csv("GIF_Annotations.csv", index=False)
print("Annotations saved to GIF_Annotations.csv")

NameError: name 'metadata' is not defined